In [28]:
import pandas as pd

# NLP
from nltk import tokenize

# Keras and TF
import keras as K
from sklearn.model_selection import train_test_split
from keras.backend.tensorflow_backend import set_session
import tensorflow as tf


# GPU usage
config = tf.ConfigProto()
config.gpu_options.allow_growth = True
set_session(tf.Session(config=config))

In [29]:

# Load training data frame
train_data_path = '..\\..\\dat\\train.tsv'
train_df = pd.read_table(train_data_path)
print('Training DataFrame loaded')

Training DataFrame loaded


In [3]:
print('Data shape:')
print(train_df.shape)

Data shape:
(1482535, 8)


In [4]:
print('Sample:')
#print(train_df.head(10))
#print(train_df.head())
#train_df.head()
train_df.head(10)

Sample:


train_id                                    name  item_condition_id  \
0         0     MLB Cincinnati Reds T Shirt Size XL                  3   
1         1        Razer BlackWidow Chroma Keyboard                  3   
2         2                          AVA-VIV Blouse                  1   
3         3                   Leather Horse Statues                  1   
4         4                    24K GOLD plated rose                  1   
5         5        Bundled items requested for Ruie                  3   
6         6      Acacia pacific tides santorini top                  3   
7         7    Girls cheer and tumbling bundle of 7                  3   
8         8                   Girls Nike Pro shorts                  3   
9         9  Porcelain clown doll checker pants VTG                  3   

                                       category_name       brand_name  price  \
0                                  Men/Tops/T-shirts              NaN   10.0   
1  Electronics/Computers & Tablets/Components & P...            Razer   52.0   
2                        Women/Tops & Blouses/Blouse           Target   10.0   
3                 Home/Home Décor/Home Décor Accents              NaN   35.0   
4                            Women/Jewelry/Necklaces              NaN   44.0   
5                                  Women/Other/Other              NaN   59.0   
6                           Women/Swimwear/Two-Piece  Acacia Swimwear   64.0   
7                    Sports & Outdoors/Apparel/Girls            Soffe    6.0   
8                    Sports & Outdoors/Apparel/Girls             Nike   19.0   
9           Vintage & Collectibles/Collectibles/Doll              NaN    8.0   

   shipping                                   item_description  
0         1                                 No description yet  
1         0  This keyboard is in great condition and works ...  
2         1  Adorable top with a hint of lace and a key hol...  
3         1  New with tags. Leather horses. Retail for [rm]...  
4         0          Complete with certificate of authenticity  
5         0  Banana republic bottoms, Candies skirt with ma...  
6         0  Size small but straps slightly shortened to fi...  
7         1  You get three pairs of Sophie cheer shorts siz...  
8         0   Girls Size small Plus green. Three shorts total.  
9         0  I realized his pants are on backwards after th...

In [30]:
# Filter on the text or item_description
X = train_df['item_description']

In [31]:
# Filter on the target prices
Y = train_df['price']

In [14]:
assert len(X) == len(Y)

In [24]:
# Preprocessing
MAX_SENT_LENGTH = 100
MAX_SENTS = 15
MAX_NB_WORDS = 20000
EMBEDDING_DIM = 100
VALIDATION_SPLIT = 0.2
NUM_EPOCHS = 100
BATCH_SIZE = 50
def clean_str(string):
    """
    Tokenization/string cleaning for dataset
    Every dataset is lower cased except
    """
    string = re.sub(r"\\", "", string)    
    string = re.sub(r"\'", "", string)    
    string = re.sub(r"\"", "", string)    
    return string.strip().lower()

In [ ]:

reviews = []
labels = []
texts = []

for idx in range(X.shape[0]):
    text = X[idx]
    print(text)
    texts.append(text)
    sentences = tokenize.sent_tokenize(text)
    reviews.append(sentences)
    
    labels.append(Y[idx])

tokenizer = Tokenizer(nb_words=MAX_NB_WORDS)
tokenizer.fit_on_texts(texts)

data = np.zeros((len(texts), MAX_SENTS, MAX_SENT_LENGTH), dtype='int32')

for i, sentences in enumerate(reviews):
    for j, sent in enumerate(sentences):
        if j< MAX_SENTS:
            wordTokens = text_to_word_sequence(sent)
            k=0
            for _, word in enumerate(wordTokens):
                if k<MAX_SENT_LENGTH and tokenizer.word_index[word]<MAX_NB_WORDS:
                    data[i,j,k] = tokenizer.word_index[word]
                    k=k+1                    
                    
word_index = tokenizer.word_index
print('Total %s unique tokens.' % len(word_index))


No description yet
This keyboard is in great condition and works like it came out of the box. All of the ports are tested and work perfectly. The lights are customizable via the Razer Synapse app on your PC.
Adorable top with a hint of lace and a key hole in the back! The pale pink is a 1X, and I also have a 3X available in white!
New with tags. Leather horses. Retail for [rm] each. Stand about a foot high. They are being sold as a pair. Any questions please ask. Free shipping. Just got out of storage
Complete with certificate of authenticity
Banana republic bottoms, Candies skirt with matching blazer,Amy Byers suit, Loft bottoms and cami top.
Size small but straps slightly shortened to fit xs, besides that, perfect condition
You get three pairs of Sophie cheer shorts size small and medium girls and two sports bra/boy shorts spandex matching sets in small and medium girls. All items total retail for [rm] in store and you can take him today for less than the price of one item at the sto

In [16]:
# Split into train and test
'''
random_seed=42
X_train, X_val, Y_train, Y_val = train_test_split(X, Y, test_size=0.33, shuffle=True, random_state=random_seed)
'''

In [ ]:
class AttLayer(Layer):
    def __init__(self, **kwargs):
        self.init = initializations.get('normal')
        super(AttLayer, self).__init__(**kwargs)

    def build(self, input_shape):
        assert len(input_shape)==3
        self.W = self.init((input_shape[-1],1))
        self.trainable_weights = [self.W]
        super(AttLayer, self).build(input_shape)  # be sure you call this somewhere!

    def call(self, x, mask=None):
        eij = K.tanh(K.dot(x, self.W))
        
        ai = K.exp(eij)
    weights = ai/tf.expand_dims(K.sum(ai, axis=1), 1)
        
    weighted_input = x*weights
    return tf.reduce_sum(weighted_input, axis=1)

    def get_output_shape_for(self, input_shape):
        return (input_shape[0], input_shape[-1])

# define base model
def baseline_model():
    GLOVE_DIR = "../dat/glove"
    embeddings_index = {}
    f = open(os.path.join(GLOVE_DIR, 'glove.6B.100d.txt'))
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        embeddings_index[word] = coefs

    f.close()

    print('Total %s word vectors.' % len(embeddings_index))


    # building Hierachical Attention network
    embedding_matrix = np.random.random((len(word_index) + 1, EMBEDDING_DIM))
    for word, i in word_index.items():
        embedding_vector = embeddings_index.get(word)
        if embedding_vector is not None:
            # words not found in embedding index will be all-zeros.
            embedding_matrix[i] = embedding_vector

    embedding_layer = Embedding(len(word_index) + 1,
                                EMBEDDING_DIM,
                                weights=[embedding_matrix],
                                input_length=MAX_SENT_LENGTH,
                                trainable=True)
    
    sentence_input = Input(shape=(MAX_SENT_LENGTH,), dtype='int32')
    embedded_sequences = embedding_layer(sentence_input)
    l_lstm = Bidirectional(GRU(100, return_sequences=True))(embedded_sequences)
    l_dense = TimeDistributed(Dense(200))(l_lstm)
    l_att = AttLayer()(l_dense)
    sentEncoder = Model(sentence_input, l_att)

    review_input = Input(shape=(MAX_SENTS,MAX_SENT_LENGTH), dtype='int32')
    review_encoder = TimeDistributed(sentEncoder)(review_input)
    l_lstm_sent = Bidirectional(GRU(100, return_sequences=True))(review_encoder)
    l_dense_sent = TimeDistributed(Dense(200))(l_lstm_sent)
    l_att_sent = AttLayer()(l_dense_sent)
    preds = Dense(1)(l_att_sent)
    model = Model(review_input, preds)

    model.compile(loss='mean_squared_error',
                  optimizer='adam',
                  metrics=['acc'])

    return model

In [ ]:
# fix random seed for reproducibility
seed = 7
numpy.random.seed(seed)
# evaluate model with standardized dataset
estimator = KerasRegressor(build_fn=baseline_model, nb_epoch=100, batch_size=5, verbose=0)


In [ ]:

kfold = KFold(n_splits=10, random_state=seed)
results = cross_val_score(estimator, data, Y, cv=kfold)
print("Results: %.2f (%.2f) MSE" % (results.mean(), results.std()))